In [ ]:
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
!kaggle datasets download -d akash2sharma/tiny-imagenet
import zipfile
zip_ref = zipfile.ZipFile('/content/tiny-imagenet.zip', 'r')
zip_ref.extractall('/content')
zip_ref.close()

cp: cannot stat 'kaggle.json': No such file or directory
Dataset URL: https://www.kaggle.com/datasets/akash2sharma/tiny-imagenet
License(s): unknown
 98% 465M/474M [00:10<00:00, 49.5MB/s]
100% 474M/474M [00:10<00:00, 48.9MB/s]


In [ ]:
import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.applications import ResNet152V2
from tensorflow.keras.models import Model, Sequential
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D
from tensorflow.keras.optimizers import Adam
from  sklearn.model_selection import train_test_split
from keras.utils import load_img, img_to_array, array_to_img
import numpy as np
from tqdm import tqdm
import os

In [ ]:
mapping_path = '/content/tiny-imagenet-200/words.txt'
class_mapping_dict = {}
class_mapping_dict_number = {}
mapping_class_to_number = {}
mapping_number_to_class = {}
i=0
for line in open(mapping_path):
   class_mapping_dict[line[:9].strip()] = line[9:].strip()
   class_mapping_dict_number[i] = line[9:].strip()
   mapping_class_to_number[line[:9].strip()] = i
   mapping_number_to_class[i] = line[:9].strip()
   i+=1
print(class_mapping_dict)
print(class_mapping_dict_number)
print(mapping_class_to_number)
print(mapping_number_to_class)

{'n00001740': 'entity', 'n00001930': 'physical entity', 'n00002137': 'abstraction, abstract entity', 'n00002452': 'thing', 'n00002684': 'object, physical object', 'n00003553': 'whole, unit', 'n00003993': 'congener', 'n00004258': 'living thing, animate thing', 'n00004475': 'organism, being', 'n00005787': 'benthos', 'n00005930': 'dwarf', 'n00006024': 'heterotroph', 'n00006150': 'parent', 'n00006269': 'life', 'n00006400': 'biont', 'n00006484': 'cell', 'n00007347': 'causal agent, cause, causal agency', 'n00007846': 'person, individual, someone, somebody, mortal, soul', 'n00015388': 'animal, animate being, beast, brute, creature, fauna', 'n00017222': 'plant, flora, plant life', 'n00019046': 'native', 'n00019128': 'natural object', 'n00019613': 'substance', 'n00020090': 'substance', 'n00020827': 'matter', 'n00021265': 'food, nutrient', 'n00021734': 'nutrient', 'n00021939': 'artifact, artefact', 'n00022903': 'article', 'n00023100': 'psychological feature', 'n00023271': 'cognition, knowledge, 

In [ ]:
src_path_train = '/content/tiny-imagenet-200/train'
src_path_test = '/content/tiny-imagenet-200/val'
val_dir = '/content/tiny-imagenet-200/val'
# # Creation of dataset_array and CLASSES

# CLASSES = []
# images_array = []
# for train_class in tqdm(os.listdir(src_path_train)):
#     i = 0
#     for el in os.listdir(src_path_train + '/' + train_class):
#         if i < 10:
#             path = src_path_train + '/' + train_class + '/' + el
#             image = load_img(path,target_size=(224,224,3))
#             image_array = img_to_array(image).astype(np.uint8)
#             images_array.append(image_array)
#             CLASS = class_mapping_dict[path.split('/')[-2]]
#             CLASSES.append(CLASS)
#             i+=1
#         else:
#             break
# images_array = np.array(images_array)
# CLASSES = np.array(CLASSES)

In [ ]:
batch_size = 128
epochs = 5
# Create ImageDataGenerators
image_gen = ImageDataGenerator(
    rescale=1./255,
    shear_range=0.2,
    zoom_range=0.2,
    horizontal_flip=True,
    validation_split=0.2
)

val_datagen = ImageDataGenerator(rescale=1./255)

train_generator = image_gen.flow_from_directory(
  src_path_train,
  target_size=(224,224),
  shuffle=True,
  batch_size=batch_size,
  subset="training",
  class_mode="sparse"
)

val_generator = image_gen.flow_from_directory(
  src_path_train,
  target_size=(224,224),
  shuffle=True,
  batch_size=batch_size,
  subset="validation",
  class_mode="sparse"
)

# Verify the number of classes
print(f"Training classes: {len(train_generator.class_indices)}")
print(f"Validation classes: {len(val_generator.class_indices)}")

Found 80000 images belonging to 200 classes.
Found 20000 images belonging to 200 classes.
Training classes: 200
Validation classes: 200


In [ ]:
# import os
# import shutil

# def organize_images(src_dir, dest_dir):
#     if not os.path.exists(dest_dir):
#         os.makedirs(dest_dir)

#     for root, dirs, files in os.walk(src_dir):
#         for file in files:
#             if file.endswith('.jpg') or file.endswith('.jpeg') or file.endswith('.png'):
#                 class_name = os.path.basename(root)
#                 class_dir = os.path.join(dest_dir, class_name)

#                 if not os.path.exists(class_dir):
#                     os.makedirs(class_dir)

#                 src_file_path = os.path.join(root, file)
#                 dest_file_path = os.path.join(class_dir, file)

#                 shutil.copy2(src_file_path, dest_file_path)

#     print(f"Images successfully organized into {dest_dir}")

# # Set the paths to your Tiny ImageNet dataset
# tiny_imagenet_dir = '/content/tiny-imagenet-200'  # Update this with your actual path
# train_src_dir = os.path.join(tiny_imagenet_dir, '/content/tiny-imagenet-200/train')
# val_src_dir = os.path.join(tiny_imagenet_dir, '/content/tiny-imagenet-200/val/images')  # Adjust if necessary

# train_dest_dir = '/content/train'  # Destination directory for training images
# val_dest_dir = '/content/val'  # Destination directory for validation images

# # Organize the images
# organize_images(train_src_dir, train_dest_dir)
# organize_images(val_src_dir, val_dest_dir)


In [ ]:
# Load ResNet152V2 with pre-trained weights from ImageNet
base_model = ResNet152V2(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

# Add global average pooling layer
x = base_model.output
x = GlobalAveragePooling2D()(x)

# Add a fully connected layer with 200 units (for 200 classes) and a softmax activation function
predictions = Dense(200, activation='softmax')(x)

# Define the final model
model = Model(inputs=base_model.input, outputs=predictions)

# Freeze the base model layers
for layer in base_model.layers:
    layer.trainable = False

# Compile the model
model.compile(optimizer=Adam(), loss='sparse_categorical_crossentropy', metrics=['accuracy'])

# Print model summary
model.summary()




234545216/234545216 ━━━━━━━━━━━━━━━━━━━━ 1s 0us/step


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)              ┃ Output Shape           ┃        Param # ┃ Connected to           ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer (InputLayer)  │ (None, 224, 224, 3)    │              0 │ -                      │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv1_pad (ZeroPadding2D) │ (None, 230, 230, 3)    │              0 │ input_layer[0][0]      │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv1_conv (Conv2D)       │ (None, 112, 112, 64)   │          9,472 │ conv1_pad[0][0]        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ pool1_pad (ZeroPadding2D) │ (None, 114, 114, 64)   │              0 │ conv1_conv[0][0]       │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ pool1_pool (MaxPooling2D) │ (None, 56, 56, 64)     │              0 │ pool1_pad[0][0]        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2_block1_preact_bn    │ (None, 56, 56, 64)     │            256 │ pool1_pool[0][0]       │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2_block1_preact_relu  │ (None, 56, 56, 64)     │              0 │ conv2_block1_preact_b… │
│ (Activation)              │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2_block1_1_conv       │ (None, 56, 56, 64)     │          4,096 │ conv2_block1_preact_r… │
│ (Conv2D)                  │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2_block1_1_bn         │ (None, 56, 56, 64)     │            256 │ conv2_block1_1_conv[0… │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2_block1_1_relu       │ (None, 56, 56, 64)     │              0 │ conv2_block1_1_bn[0][… │
│ (Activation)              │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2_block1_2_pad        │ (None, 58, 58, 64)     │              0 │ conv2_block1_1_relu[0… │
│ (ZeroPadding2D)           │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2_block1_2_conv       │ (None, 56, 56, 64)     │         36,864 │ conv2_block1_2_pad[0]… │
│ (Conv2D)                  │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2_block1_2_bn         │ (None, 56, 56, 64)     │            256 │ conv2_block1_2_conv[0… │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2_block1_2_relu       │ (None, 56, 56, 64)     │              0 │ conv2_block1_2_bn[0][… │
│ (Activation)              │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2_block1_0_conv       │ (None, 56, 56, 256)    │         16,640 │ conv2_block1_preact_r… │
│ (Conv2D)             

 Total params: 58,741,448 (224.08 MB)

 Trainable params: 409,800 (1.56 MB)

 Non-trainable params: 58,331,648 (222.52 MB)

In [ ]:
history = model.fit(
    train_generator,
    epochs=10,  # Adjust as needed
    validation_data=val_generator
 )

Epoch 1/10


/usr/local/lib/python3.10/dist-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


625/625 ━━━━━━━━━━━━━━━━━━━━ 1348s 2s/step - accuracy: 0.4551 - loss: 2.5511 - val_accuracy: 0.6329 - val_loss: 1.5093
Epoch 2/10
625/625 ━━━━━━━━━━━━━━━━━━━━ 1302s 2s/step - accuracy: 0.6752 - loss: 1.2858 - val_accuracy: 0.6417 - val_loss: 1.4594
Epoch 3/10
625/625 ━━━━━━━━━━━━━━━━━━━━ 1286s 2s/step - accuracy: 0.7070 - loss: 1.1329 - val_accuracy: 0.6503 - val_loss: 1.4548
Epoch 4/10
625/625 ━━━━━━━━━━━━━━━━━━━━ 1275s 2s/step - accuracy: 0.7330 - loss: 1.0101 - val_accuracy: 0.6484 - val_loss: 1.4749
Epoch 5/10
625/625 ━━━━━━━━━━━━━━━━━━━━ 1272s 2s/step - accuracy: 0.7444 - loss: 0.9527 - val_accuracy: 0.6501 - val_loss: 1.4704
Epoch 6/10
625/625 ━━━━━━━━━━━━━━━━━━━━ 1268s 2s/step - accuracy: 0.7579 - loss: 0.8910 - val_accuracy: 0.6533 - val_loss: 1.4824
Epoch 7/10
625/625 ━━━━━━━━━━━━━━━━━━━━ 1264s 2s/step - accuracy: 0.7702 - loss: 0.8387 - val_accuracy: 0.6491 - val_loss: 1.5120
Epoch 8/10
625/625 ━━━━━━━━━━━━━━━━━━━━ 1261s 2s/step - accuracy: 0.7769 - loss: 0.8094 - val_accurac

In [ ]:
model.save('my_model.h5')